In [1]:
import itertools
import pandas as pd
import numpy as np
import toytree
import toyplot
import arviz as az
import pymc3 as pm

### Tree and dataframe setup

In [2]:
# generate a random tree
NSPECIES = 80
TREE = toytree.rtree.bdtree(
    ntips=NSPECIES,
    seed=666,
).mod.node_scale_root_height(1.0)

# node idxs that delimit several distinct clades on this tree
CLADES = [152, 153, 154, 155]

# draw and color the four major clades
TREE.draw(
    layout='d', 
    width=500,
    tip_labels=False,
    edge_colors=TREE.get_edge_values_mapped({
        j: toytree.colors[i] for i, j in enumerate(CLADES)
    }),
    scalebar=True,
);

<svg class="toyplot-canvas-Canvas" height="250.0px" id="td97a0ff03bb54f599759f86627499d90" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 500.0 250.0" width="500.0px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> 0.0 0.5 1.0

In [3]:
# make group index (gidx)
crown_dict = {i: TREE.get_tip_labels(i) for i in CLADES}
gidx = np.zeros(TREE.ntips, dtype=int)
for tidx, tip in enumerate(TREE.get_tip_labels()):
    for cidx, clade in enumerate(crown_dict):
        if tip in crown_dict[clade]:
            gidx[tidx] = cidx
gidx

array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2,
       3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3])

In [4]:
# True param values
𝛼_mean = 0.05
𝛼_std = 0.02
𝛽_mean = 3.0
𝛽_std = 0.2
𝜓_mean = 0.0
𝜓_std = 0.33

# 4 different clade effects on rate of RI (used for partial-pooling data)
𝜓_0_mean = 1.0
𝜓_0_std = 0.1
𝜓_1_mean = 0.5
𝜓_1_std = 0.05
𝜓_2_mean = -0.5
𝜓_2_std = 0.05
𝜓_3_mean = -1.0
𝜓_3_std = 0.1

In [5]:
# species dataframe
SPECIES_DATA = pd.DataFrame({
    "gidx": gidx,
    "b": np.random.normal(𝛽_mean, 𝛽_std, TREE.ntips),
    "psi": np.random.normal(𝜓_mean, 𝜓_std, TREE.ntips),
    "psi_x": np.concatenate([
        np.random.normal(𝜓_0_mean, 𝜓_0_std, len(gidx[gidx == 0])),
        np.random.normal(𝜓_1_mean, 𝜓_1_std, len(gidx[gidx == 1])),
        np.random.normal(𝜓_2_mean, 𝜓_2_std, len(gidx[gidx == 2])),
        np.random.normal(𝜓_3_mean, 𝜓_3_std, len(gidx[gidx == 3])),
    ]),
})
SPECIES_DATA.head()

gidx         b       psi     psi_x
0     0  2.570468 -0.236524  0.997529
1     0  3.292698 -0.624017  0.863576
2     0  2.936227 -0.612795  0.956139
3     0  2.746916 -0.234236  1.115301
4     0  2.767121  0.031270  0.981499

### Generate crossing data

In [6]:
def get_dist(tree, idx0, idx1):
    "returns the genetic distance between two nodes on a tree"
    dist = tree.treenode.get_distance(
        tree.idx_dict[idx0], 
        tree.idx_dict[idx1],
    )
    return dist

# get all combinations of two sampled taxa
a, b = zip(*itertools.combinations(range(NSPECIES), 2))

# organize into DF and get genetic distance between pairs
DATA = pd.DataFrame({
    "sidx0": a,
    "sidx1": b,
    "dist": [(get_dist(TREE, i, j) / 2) for (i, j) in zip(a, b)],
})

DATA['b'] = np.random.normal(𝛽_mean, 𝛽_std, DATA.shape[0])
DATA['velo'] = (
    DATA['b']
    + SPECIES_DATA['psi'][DATA.sidx0].values
    + SPECIES_DATA['psi'][DATA.sidx1].values
)
DATA['velo_x'] = (
    DATA['b']
    + SPECIES_DATA['psi_x'][DATA.sidx0].values
    + SPECIES_DATA['psi_x'][DATA.sidx1].values
)
DATA['intercept'] = np.random.normal(𝛼_mean, 𝛼_std, DATA.shape[0])
# DATA['error'] = np.random.normal(0.0, 𝜎_std, DATA.shape[0])

# get logits
DATA['logit_b'] = (
    1 / (1 + np.exp(-(DATA.intercept * DATA.b ** DATA.dist)))
)
DATA['logit'] = (
    1 / (1 + np.exp(-(DATA.intercept * DATA.velo ** DATA.dist)))
)
DATA['logit_x'] = (
    1 / (1 + np.exp(-(DATA.intercept * DATA.velo_x ** DATA.dist)))
)

# get RI estimates
DATA['RI_pooled'] = np.random.binomial(n=1, p=DATA.logit_b / DATA.logit_b.max())
DATA['RI_unpooled'] = np.random.binomial(n=1, p=DATA.logit / DATA.logit.max())
DATA['RI_partpooled'] = np.random.binomial(n=1, p=DATA.logit_x / DATA.logit_x.max())

DATA.head()

sidx0  sidx1      dist         b      velo    velo_x  intercept   logit_b  \
0      0      1  0.073376  2.881579  2.021039  4.742684   0.023752  0.506417   
1      0      2  0.089748  2.638508  1.789189  4.592176   0.074466  0.520299   
2      0      3  0.129770  3.113867  2.643107  5.226697   0.055129  0.515966   
3      0      4  0.144542  3.059197  2.853944  5.038226   0.059521  0.517483   
4      0      5  0.144542  2.620887  2.866354  4.699434   0.059066  0.516967   

      logit   logit_x  RI_pooled  RI_unpooled  RI_partpooled  
0  0.506252  0.506656          1            0              1  
1  0.519604  0.521333          1            1              1  
2  0.515630  0.517075          1            1              1  
3  0.517309  0.518790          1            1              1  
4  0.517187  0.518459          1            1              1

In [7]:
NSAMPLES = 2000
SAMPLE = DATA.sample(NSAMPLES).copy().reset_index(drop=True)
SAMPLE.head()

sidx0  sidx1      dist         b      velo    velo_x  intercept   logit_b  \
0     60     63  0.578689  2.921440  2.625589  1.913308   0.044766  0.520801   
1     46     74  0.592720  3.287330  3.246154  1.886728   0.043472  0.521989   
2     23     30  0.438896  2.615066  2.010742  4.803178   0.057368  0.521856   
3     61     71  0.592720  3.160457  2.911351  1.778620   0.020785  0.510277   
4     23     34  0.590047  3.069562  2.832857  4.990309   0.039344  0.519055   

      logit   logit_x  RI_pooled  RI_unpooled  RI_partpooled  
0  0.519556  0.516286          1            1              1  
1  0.521826  0.515828          0            0              0  
2  0.519478  0.528527          1            0              1  
3  0.509789  0.507310          1            1              1  
4  0.518175  0.525373          1            1              1

### Visualize data

In [8]:
def logit_plot(dist, logit, RI):
    canvas = toyplot.Canvas(width=500, height=250)
    ax0 = canvas.cartesian(
        label="pooled data (function)",
        xlabel="Genetic dist.",
        ylabel="Logit function",
        grid=(1, 2, 0),
    )
    ax1 = canvas.cartesian(
        label="pooled data (observation)",
        xlabel="Genetic dist.",
        ylabel="RI",
        grid=(1, 2, 1),
    )

    # points are jittered on x-axis for visibility
    ax0.scatterplot(
        dist,
        logit,
        size=5,
        opacity=0.33,
        color=toyplot.color.Palette()[0],
    );
    ax1.scatterplot(
        dist,
        RI,
        size=10,
        opacity=0.2,
        marker="|",
        mstyle={
            "stroke": toyplot.color.Palette()[1],
            "stroke-width": 3,
        },
    );
    return canvas, (ax0, ax1)

In [9]:
logit_plot(SAMPLE.dist, SAMPLE.logit_b, SAMPLE.RI_pooled);

<svg class="toyplot-canvas-Canvas" height="250.0px" id="t50164cbf8797468b8c6fdf73aaa24b78" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 500.0 250.0" width="500.0px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> <

In [10]:
logit_plot(SAMPLE.dist, SAMPLE.logit, SAMPLE.RI_unpooled);

<svg class="toyplot-canvas-Canvas" height="250.0px" id="t0aeddf2c0c1d416dbd3c095b92113314" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 500.0 250.0" width="500.0px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> <g class="toy

In [11]:
logit_plot(SAMPLE.dist, SAMPLE.logit_x, SAMPLE.RI_partpooled);

<svg class="toyplot-canvas-Canvas" height="250.0px" id="t654ec45156ef4a928d3daff07ced2bb2" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 500.0 250.0" width="500.0px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> <g class="t

### Define models

In [33]:
def pooled_logistic(x, y, **kwargs):
    
    # define model
    with pm.Model() as model:  

        # parameters and error
        𝛼 = pm.Normal('𝛼', mu=0., sigma=10., shape=1)
        𝛽 = pm.Normal('𝛽', mu=0.5, sigma=10, shape=1)
        # 𝛽 = pm.Normal('𝛽', mu=0., sigma=10., shape=1)
        
        # link function
        effect = 𝛼 * (𝛽 ** x)
        logit = pm.Deterministic("logit", pm.invlogit(effect))
        
        # data likelihood
        y = pm.Bernoulli("y", p=logit, observed=y)
        
        # sample posterior, skip burnin
        trace = pm.sample(init = 'adapt_diag', **kwargs)[1000:]
    
        # show summary table
        stats = pm.summary(trace)
    
    # organize results
    result_dict = {
        'model': model, 
        'trace': trace,
        'stats': stats,
    }
    return result_dict

In [19]:
def unpooled_logistic(x, y, idx0, idx1, **kwargs):
    
    # define model
    with pm.Model() as model:
        
        # indexers
        sidx0 = pm.Data("spp_idx0", idx0.values)
        sidx1 = pm.Data("spp_idx1", idx1.values)

        # parameters and error
        𝜓_mean = pm.Normal('𝜓_mean', mu=0., sigma=5., shape=1)
        𝜓_std = pm.HalfNormal('𝜓_std', 5., shape=1)
        𝜓_offset = pm.Normal('𝜓_offset', mu=0, sigma=1., shape=TREE.ntips)
        𝜓 = pm.Deterministic('𝜓', 𝜓_mean + 𝜓_std * 𝜓_offset)
        𝛼 = pm.Normal('𝛼', mu=0., sigma=10., shape=1)
        # 𝛽 = pm.Normal('𝛽', mu=1., sigma=10., shape=1)
        𝛽 = pm.Normal('𝛽', mu=0.5, sigma=10, shape=1)
        
        # link function
        effect = 𝛼 * ((𝛽 + 𝜓[sidx0] + 𝜓[sidx1]) ** x)
        logit = pm.Deterministic("logit", pm.invlogit(effect))
        
        # data likelihood
        y = pm.Bernoulli("y", p=logit, observed=y)
        
        # sample posterior, skip burnin
        trace = pm.sample(init = 'adapt_diag', **kwargs)[1000:]
    
        # show summary table
        stats = pm.summary(trace)
        
    # organize results
    result_dict = {
        'model': model, 
        'trace': trace,
        'stats': stats,
    }
    return result_dict

In [20]:
def partpooled_logistic(x, y, idx0, idx1, gidx, **kwargs):
    
    # define model
    with pm.Model() as model:
        
        # indexers
        sidx0 = pm.Data("spp_idx0", idx0)
        sidx1 = pm.Data("spp_idx1", idx1)
        gidx = pm.Data("gidx", gidx)

        # parameters and error
        𝜓_mean = pm.Normal('𝜓_mean', mu=0., sigma=5., shape=4)
        𝜓_std = pm.HalfNormal('𝜓_std', 5., shape=4)
        𝜓_offset = pm.Normal('𝜓_offset', mu=0, sigma=1., shape=TREE.ntips)
        𝜓 = pm.Deterministic('𝜓', 𝜓_mean[gidx] + 𝜓_std[gidx] * 𝜓_offset)
        # 𝛽 = pm.Normal('𝛽', mu=1., sigma=10., shape=1)
        𝛽 = pm.Normal('𝛽', mu=0.5., sigma=10, shape=1)
        𝛼 = pm.Normal('𝛼', mu=0., sigma=10., shape=1)
        
        # linear model prediction
        effect = 𝛼 * ((𝛽 + 𝜓[sidx0] + 𝜓[sidx1]) ** x)
        logit = pm.Deterministic("logit", pm.invlogit(effect))
        
        # data likelihood (normal distributed errors)
        y = pm.Bernoulli("y", p=logit, observed=y)

        # sample posterior, skip burnin
        trace = pm.sample(init = 'adapt_diag', **kwargs)[1000:]

        # show summary table
        stats = pm.summary(trace)
        
    # organize results
    result_dict = {
        'model': model, 
        'trace': trace,
        'stats': stats,
    }
    return result_dict

### Functions to plot results

In [15]:
def toytrace(trace, var_names, titles):
    """
    Plot posterior trace with toyplot
    """
    nvars = len(var_names)
    
    # setup canvase
    canvas = toyplot.Canvas(width=500, height=200 * nvars)
    
    # store axes
    axes = []
    
    # iter over params
    for pidx, param in enumerate(var_names):
        
        # get param posterior
        posterior = trace.get_values(param)
        
        # setup axes 
        ax = canvas.cartesian(grid=(nvars, 1, pidx))
        ax.y.show = False
        ax.x.spine.style = {"stroke-width": 1.5}
        ax.x.ticks.labels.style = {"font-size": "12px"}
        ax.x.ticks.show = True
        ax.x.label.text = f"param='{titles[pidx]}'"        
        
        # iterate over shape of param
        for idx in range(posterior.shape[1]):
            mags, bins = np.histogram(posterior[:, idx], bins=100)
            ax.plot(bins[1:], mags, stroke_width=2, opacity=0.6)
        axes.append(ax)
    return canvas, axes

In [16]:
import scipy.stats as stats

def draw_velocity_dists(trace, baseline=0.15):
    """
    Draw the clade velocities as gaussians
    """
    canvas = toyplot.Canvas(width=350, height=300)
    axes = canvas.cartesian(xlabel="Relative velocity of reproductive isolation")
    marks = []
    base = 0
    for i in range(trace['𝜓_mean'].shape[1]):
        
        loc = trace['𝜓_mean'][:, i].mean()
        scale = trace['𝜓_std'][:, i].mean()
        interval = stats.norm.interval(0.995, loc, scale)
        points = np.linspace(interval[0], interval[1], 100)
        mark = axes.fill(
            points, 
            stats.norm.pdf(points, loc=loc, scale=scale), 
            style={
                "fill-opacity": 0.45,
                "stroke": 'black',
                "stroke-opacity": 1.0,
                "stroke-width": 1,
            },
            baseline=np.repeat(base, 100),
        )
        marks.append(mark)
        axes.hlines(base, style={"stroke-dasharray": "5,5", 'stroke-width': 1})
        base += baseline
        
    axes.y.show = False
    axes.x.ticks.locator = toyplot.locator.Extended(only_inside=True)
    axes.x.ticks.show = True
    return canvas, axes, marks

In [17]:
# MCMC sampler kwargs
sample_kwargs = dict(
    tune=10000,
    draws=10000,
    target_accept=0.99,
    return_inferencedata=False,
    progressbar=True,
)

### Run three datasets under pooled model

In [34]:
# model input
model_args = [
    SAMPLE.dist,
    SAMPLE.RI_pooled,
    SAMPLE.sidx0,
    SAMPLE.sidx1,
    gidx
]

# pooled model
pooled_model_pooled_data = pooled_logistic(*model_args[:2], **sample_kwargs)

Auto-assigning NUTS sampler...
Initializing NUTS using adapt_diag...
Multiprocess sampling (4 chains in 4 jobs)
NUTS: [𝛽, 𝛼]


Sampling 4 chains for 10_000 tune and 10_000 draw iterations (40_000 + 40_000 draws total) took 623 seconds.
The number of effective samples is smaller than 25% for some parameters.


In [35]:
# model input
model_args = [
    SAMPLE.dist,
    SAMPLE.RI_unpooled,
    SAMPLE.sidx0,
    SAMPLE.sidx1,
    gidx
]

# pooled model
pooled_model_unpooled_data = pooled_logistic(*model_args[:2], **sample_kwargs)

Auto-assigning NUTS sampler...
Initializing NUTS using adapt_diag...
Multiprocess sampling (4 chains in 4 jobs)
NUTS: [𝛽, 𝛼]


Sampling 4 chains for 10_000 tune and 10_000 draw iterations (40_000 + 40_000 draws total) took 649 seconds.
The number of effective samples is smaller than 25% for some parameters.


In [36]:
# model input
model_args = [
    SAMPLE.dist,
    SAMPLE.RI_partpooled,
    SAMPLE.sidx0,
    SAMPLE.sidx1,
    gidx
]

# pooled model
pooled_model_partpooled_data = pooled_logistic(*model_args[:2], **sample_kwargs)

Auto-assigning NUTS sampler...
Initializing NUTS using adapt_diag...
Multiprocess sampling (4 chains in 4 jobs)
NUTS: [𝛽, 𝛼]


Sampling 4 chains for 10_000 tune and 10_000 draw iterations (40_000 + 40_000 draws total) took 583 seconds.
The number of effective samples is smaller than 25% for some parameters.


### Run three datasets under unpooled model

In [21]:
# model input
model_args = [
    SAMPLE.dist,
    SAMPLE.RI_pooled,
    SAMPLE.sidx0,
    SAMPLE.sidx1,
    gidx
]

# unpooled model
unpooled_model_pooled_data = unpooled_logistic(*model_args[:4], **sample_kwargs)

Auto-assigning NUTS sampler...
Initializing NUTS using adapt_diag...
Multiprocess sampling (4 chains in 4 jobs)
NUTS: [𝛽, 𝛼, 𝜓_offset, 𝜓_std, 𝜓_mean]


Sampling 4 chains for 10_000 tune and 10_000 draw iterations (40_000 + 40_000 draws total) took 38252 seconds.
There were 620 divergences after tuning. Increase `target_accept` or reparameterize.
The chain reached the maximum tree depth. Increase max_treedepth, increase target_accept or reparameterize.
There were 1858 divergences after tuning. Increase `target_accept` or reparameterize.
The acceptance probability does not match the target. It is 0.9544879754472493, but should be close to 0.99. Try to increase the number of tuning steps.
The chain reached the maximum tree depth. Increase max_treedepth, increase target_accept or reparameterize.
There were 738 divergences after tuning. Increase `target_accept` or reparameterize.
The chain reached the maximum tree depth. Increase max_treedepth, increase target_accept or reparameterize.
There were 593 divergences after tuning. Increase `target_accept` or reparameterize.
The chain reached the maximum tree depth. Increase max_treedepth, incre

In [38]:
# model input
model_args = [
    SAMPLE.dist,
    SAMPLE.RI_unpooled,
    SAMPLE.sidx0,
    SAMPLE.sidx1,
    gidx
]

# unpooled model
unpooled_model_unpooled_data = unpooled_logistic(*model_args[:4], **sample_kwargs)

Auto-assigning NUTS sampler...
Initializing NUTS using adapt_diag...
Multiprocess sampling (4 chains in 4 jobs)
NUTS: [𝛽, 𝛼, 𝜓_offset, 𝜓_std, 𝜓_mean]


Sampling 4 chains for 10_000 tune and 10_000 draw iterations (40_000 + 40_000 draws total) took 35250 seconds.
There were 273 divergences after tuning. Increase `target_accept` or reparameterize.
The chain reached the maximum tree depth. Increase max_treedepth, increase target_accept or reparameterize.
There were 423 divergences after tuning. Increase `target_accept` or reparameterize.
The chain reached the maximum tree depth. Increase max_treedepth, increase target_accept or reparameterize.
There were 282 divergences after tuning. Increase `target_accept` or reparameterize.
The chain reached the maximum tree depth. Increase max_treedepth, increase target_accept or reparameterize.
There were 417 divergences after tuning. Increase `target_accept` or reparameterize.
The chain reached the maximum tree depth. Increase max_treedepth, increase target_accept or reparameterize.
The number of effective samples is smaller than 10% for some parameters.


In [40]:
# model input
model_args = [
    SAMPLE.dist,
    SAMPLE.RI_partpooled,
    SAMPLE.sidx0,
    SAMPLE.sidx1,
    gidx
]

# unpooled model
unpooled_model_partpooled_data = unpooled_logistic(*model_args[:4], **sample_kwargs)

Auto-assigning NUTS sampler...
Initializing NUTS using adapt_diag...
Multiprocess sampling (4 chains in 4 jobs)
NUTS: [𝛽, 𝛼, 𝜓_offset, 𝜓_std, 𝜓_mean]


Sampling 4 chains for 10_000 tune and 10_000 draw iterations (40_000 + 40_000 draws total) took 39308 seconds.
There were 34 divergences after tuning. Increase `target_accept` or reparameterize.
The chain reached the maximum tree depth. Increase max_treedepth, increase target_accept or reparameterize.
There were 35 divergences after tuning. Increase `target_accept` or reparameterize.
The chain reached the maximum tree depth. Increase max_treedepth, increase target_accept or reparameterize.
There were 34 divergences after tuning. Increase `target_accept` or reparameterize.
The chain reached the maximum tree depth. Increase max_treedepth, increase target_accept or reparameterize.
There were 42 divergences after tuning. Increase `target_accept` or reparameterize.
The chain reached the maximum tree depth. Increase max_treedepth, increase target_accept or reparameterize.
The number of effective samples is smaller than 25% for some parameters.


### Run three datasets under partpooled model

In [42]:
# model input
model_args = [
    SAMPLE.dist,
    SAMPLE.RI_pooled,
    SAMPLE.sidx0,
    SAMPLE.sidx1,
    gidx
]

# unpooled model
partpooled_model_pooled_data = partpooled_logistic(*model_args, **sample_kwargs)

Auto-assigning NUTS sampler...
Initializing NUTS using adapt_diag...
Multiprocess sampling (4 chains in 4 jobs)
NUTS: [𝛼, 𝛽, 𝜓_offset, 𝜓_std, 𝜓_mean]


Sampling 4 chains for 10_000 tune and 10_000 draw iterations (40_000 + 40_000 draws total) took 13587 seconds.
There were 9808 divergences after tuning. Increase `target_accept` or reparameterize.
There were 8796 divergences after tuning. Increase `target_accept` or reparameterize.
There were 9292 divergences after tuning. Increase `target_accept` or reparameterize.
There were 9516 divergences after tuning. Increase `target_accept` or reparameterize.
The number of effective samples is smaller than 10% for some parameters.


In [43]:
# model input
model_args = [
    SAMPLE.dist,
    SAMPLE.RI_unpooled,
    SAMPLE.sidx0,
    SAMPLE.sidx1,
    gidx
]

# unpooled model
partpooled_model_unpooled_data = partpooled_logistic(*model_args, **sample_kwargs)

Auto-assigning NUTS sampler...
Initializing NUTS using adapt_diag...
Multiprocess sampling (4 chains in 4 jobs)
NUTS: [𝛼, 𝛽, 𝜓_offset, 𝜓_std, 𝜓_mean]


Sampling 4 chains for 10_000 tune and 10_000 draw iterations (40_000 + 40_000 draws total) took 19781 seconds.
There were 8422 divergences after tuning. Increase `target_accept` or reparameterize.
There were 8916 divergences after tuning. Increase `target_accept` or reparameterize.
There were 9047 divergences after tuning. Increase `target_accept` or reparameterize.
There were 8698 divergences after tuning. Increase `target_accept` or reparameterize.
The number of effective samples is smaller than 10% for some parameters.


In [ ]:
# model input
model_args = [
    SAMPLE.dist,
    SAMPLE.RI_partpooled,
    SAMPLE.sidx0,
    SAMPLE.sidx1,
    gidx
]

# unpooled model
partpooled_model_partpooled_data = partpooled_logistic(*model_args, **sample_kwargs)

Auto-assigning NUTS sampler...
Initializing NUTS using adapt_diag...
Multiprocess sampling (4 chains in 4 jobs)
NUTS: [𝛼, 𝛽, 𝜓_offset, 𝜓_std, 𝜓_mean]


In [27]:
partpooled_model_partpooled_data['stats']

mean     sd  hdi_3%  hdi_97%  mcse_mean  mcse_sd  ess_mean  \
𝜓_mean[0]   -0.347  2.226  -4.545    3.757      0.038    0.027    3488.0   
𝜓_mean[1]   -0.467  2.226  -4.677    3.664      0.038    0.027    3490.0   
𝜓_mean[2]   -0.293  2.223  -4.497    3.829      0.038    0.027    3495.0   
𝜓_mean[3]   -0.360  2.225  -4.570    3.733      0.038    0.027    3495.0   
𝜓_offset[0]  0.389  0.985  -1.384    2.292      0.010    0.008    9773.0   
...            ...    ...     ...      ...        ...      ...       ...   
logit[1995]  0.862  0.020   0.824    0.897      0.000    0.000   12700.0   
logit[1996]  0.853  0.018   0.817    0.886      0.000    0.000   10400.0   
logit[1997]  0.877  0.025   0.829    0.922      0.000    0.000   12670.0   
logit[1998]  0.867  0.027   0.815    0.915      0.000    0.000   12283.0   
logit[1999]  0.905  0.032   0.848    0.967      0.000    0.000   11391.0   

              ess_sd  ess_bulk  ess_tail  r_hat  
𝜓_mean[0]     3488.0    3493.0    5415.0    1.0  
𝜓_mean[1]     3490.0    3493.0    5248.0    1.0  
𝜓_mean[2]     3495.0    3498.0    5396.0    1.0  
𝜓_mean[3]     3495.0    3502.0    5323.0    1.0  
𝜓_offset[0]   7257.0    9716.0    7711.0    1.0  
...              ...       ...       ...    ...  
logit[1995]  12700.0   12962.0   15390.0    1.0  
logit[1996]  10400.0   10457.0   13046.0    1.0  
logit[1997]  12670.0   12780.0   14999.0    1.0  
logit[1998]  12265.0   12276.0   16667.0    1.0  
logit[1999]  11242.0   10819.0   10947.0    1.0  

[2170 rows x 11 columns]

In [28]:
toytrace(partpooled_model_partpooled_data['trace'], ['𝜓_mean', '𝜓_offset', '𝜓'], ['psi-mean', 'psi-offset', 'psi-spp']);

<svg class="toyplot-canvas-Canvas" height="600.0px" id="t402358700dc0478083636e1c6630b7ac" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 500.0 600.0" width="500.0px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> <path d="M 85.7261069014011 149.74937343358397 L 89.29381295341365 149.58228905597326 L 92.86151900542625 149.66583124477862 L 96.42922505743883 150.0 L 99.9969311094514 149.16457811194653 L 103.56463716146396 149.33166248955723 L 107.13234321347655 148.5797827903091 L 110.70004926548913 148.83040935672514 L 114.26775531750172 148.9139515455305 L 117.83546136951429 147.827903091061 L 121.40316742152686 147.3266499582289 L 124.97087347353944 147.99498746867167 L 128.53857952555202 146.49122807017542 L 132.10628557756462 145.3216374269006 L 135.67399162957716 145.40517961570592 L 139.24169768158976 143.65079365079364 L 142.80940373360235 143.2330827067669 L 146.3771097856149 140.55973266499583 L 149.9448158376275 141.14452798663325 L 153.51252188964008 139.30659983291565 L 157.08022794165265 136.7167919799499 L 160.64793399366522 133.04093567251465 L 164.21564004567784 132.03842940685047 L 167.78334609769038 128.86382623224728 L 171.35105214970292 126.02339181286551 L 174.91875820171555 123.68421052631581 L 178.48646425372812 119.17293233082705 L 182.0541703057407 116.16541353383458 L 185.62187635775325 107.3934837092732 L 189.18958240976585 104.88721804511279 L 192.75728846177844 102.7986633249791 L 196.324994513791 100.9607351712615 L 199.89270056580358 95.11278195488721 L 203.46040661781615 82.49791144527987 L 207.02811266982874 84.92063492063491 L 210.5958187218413 78.57142857142857 L 214.16352477385388 74.64494569757727 L 217.73123082586648 68.37928153717627 L 221.29893687787904 63.78446115288221 L 224.86664292989158 58.9390142021721 L 228.4343489819042 59.106098579782795 L 232.0020550339168 58.68838763575606 L 235.56976108592937 62.94903926482874 L 239.13746713794194 52.42272347535506 L 242.7051731899545 56.09857978279032 L 246.2728792419671 50.0 L 249.84058529397964 56.51629072681704 L 253.40829134599227 57.01754385964912 L 256.97599739800484 53.675856307435254 L 260.5437034500174 60.526315789473685 L 264.11140950203 59.44026733500418 L 267.67911555404254 63.9515455304929 L 271.2468216060551 66.29072681704261 L 274.81452765806773 72.13868003341688 L 278.3822337100803 81.41186299081036 L 281.94993976209287 81.24477861319966 L 285.51764581410544 84.83709273182959 L 289.08535186611806 93.02422723475357 L 292.65305791813057 99.62406015037593 L 296.22076397014314 100.4594820384294 L 299.78847002215576 107.14285714285714 L 303.3561760741684 110.65162907268171 L 306.9238821261809 111.40350877192982 L 310.4915881781935 118.75522138680033 L 314.05929423020615 119.42355889724311 L 317.62700028221866 122.43107769423558 L 321.1947063342312 125.93984962406016 L 324.7624123862438 129.69924812030075 L 328.33011843825636 135.29657477025899 L 331.89782449026893 136.9674185463659 L 335.46553054228156 139.640768588137 L 339.0332365942942 141.64578111946534 L 342.60094264630675 140.97744360902257 L 346.16864869831926 143.734335839599 L 349.7363547503319 144.65329991645783 L 353.30406080234445 145.73934837092733 L 356.871766854357 147.24310776942355 L 360.4394729063696 147.15956558061822 L 364.00717895838216 145.906432748538 L 367.5748850103948 147.15956558061822 L 371.14259106240735 147.99498746867167 L 374.71029711441986 148.83040935672514 L 378.2780031664325 148.83040935672514 L 381.8457092184451 149.24812030075185 L 385.41341527045756 148.99749373433585 L 388.98112132247024 149.4987468671679 L 392.5488273744828 149.58228905597326 L 396.1165334264954 149.74937343358397 L 399.6842394785079 149.5822890559

In [29]:
# show plot of TRUE vs. ESTIMATED rates
c, a, m = toyplot.scatterplot(
    partpooled_model_partpooled_data['trace']['𝜓'].mean(axis=0),         # estimated
    SPECIES_DATA['psi_x'],                             # true
    width=400,
    height=250,
    xlabel="ESTIMATED species velocity",
    ylabel="TRUE species velocity",
    color=[toyplot.color.Palette()[i] for i in SPECIES_DATA.gidx],
);

<svg class="toyplot-canvas-Canvas" height="250.0px" id="ta5bfaf058b95410b8b937ddbcacd9696" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 400.0 250.0" width="400.0px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> -0.6 -0.5 -0.4 -0.3 -0.2 ESTIMATED species velocity -1 0 1 TRUE species velocity

In [52]:
stats.linregress(partpooled_model_partpooled_data['trace']['𝜓'].mean(axis=0), SPECIES_DATA['psi_x'])

LinregressResult(slope=-2.063394533097704, intercept=-0.51175679393135, rvalue=-0.17856765368695632, pvalue=0.11301476689211955, stderr=1.2873461573695903)

In [64]:
from scipy.stats import f_oneway
from statsmodels.stats.multicomp import pairwise_tukeyhsd

In [57]:
clade1 = partpooled_model_partpooled_data['trace']['𝜓'].mean(axis=0)[:36]
clade2 = partpooled_model_partpooled_data['trace']['𝜓'].mean(axis=0)[36:45]
clade3 = partpooled_model_partpooled_data['trace']['𝜓'].mean(axis=0)[45:66]
clade4 = partpooled_model_partpooled_data['trace']['𝜓'].mean(axis=0)[66:]

In [65]:
f_oneway(clade1, clade2, clade3, clade4)

F_onewayResult(statistic=21.4506729135739, pvalue=3.6333656668455994e-10)

In [66]:
tukey = pairwise_tukeyhsd(endog = partpooled_model_partpooled_data['trace']['𝜓'].mean(axis=0),
                          groups = gidx,
                          alpha = 0.05)
print(tukey)

Multiple Comparison of Means - Tukey HSD, FWER=0.05 
group1 group2 meandiff p-adj   lower   upper  reject
----------------------------------------------------
     0      1  -0.1204  0.001 -0.1742 -0.0667   True
     0      2    0.054 0.0033  0.0144  0.0936   True
     0      3  -0.0127 0.8716 -0.0581  0.0327  False
     1      2   0.1745  0.001   0.117  0.2319   True
     1      3   0.1077  0.001  0.0461  0.1693   True
     2      3  -0.0667  0.004 -0.1165  -0.017   True
----------------------------------------------------


In [30]:
draw_velocity_dists(partpooled_model_partpooled_data['trace'], baseline = 1.2);

<svg class="toyplot-canvas-Canvas" height="300.0px" id="t68c984b5e8c14f2bb27144835b10e12b" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 350.0 300.0" width="350.0px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> <polygon points="113.31129604599087,250.0 114.77844915234988,250.0 116.24560225870891,250.0 117.71275536506792,250.0 119.17990847142693,250.0 120.64706157778593,250.0 122.11421468414493,250.0 123.58136779050395,250.0 125.04852089686295,250.0 126.51567400322196,250.0 127.982827109581,250.0 129.44998021594,250.0 130.917133322299,250.0 132.38428642865802,250.0 133.85143953501705,250.0 135.31859264137606,250.0 136.78574574773506,250.0 138.25289885409407,250.0 139.72005196045308,250.0 141.18720506681208,250.0 142.65435817317112,250.0 144.1215112795301,250.0 145.5886643858891,250.0 147.05581749224814,250.0 148.52297059860715,250.0 149.99012370496615,250.0 151.45727681132516,250.0 152.92442991768417,250.0 154.3915830240432,250.0 155.85873613040218,250.0 157.3258892367612,250.0 158.79304234312025,250.0 160.2601954494792,250.0 161.72734855583826,250.0 163.19450166219724,250.0 164.66165476855628,250.0 166.12880787491528,250.0 167.5959609812743,250.0 169.0631140876333,250.0 170.5302671939923,250.0 171.99742030035134,250.0 173.46457340671034,250.0 174.93172651306935,250.0 176.39887961942833,250.0 177.86603272578736,250.0 179.33318583214637,250.0 180.8003389385054,250.0 182.26749204486438,250.0 183.73464515122342,250.0 185.20179825758242,250.0 186.6689513639414,250.0 188.13610447030044,250.0 189.60325757665944,250.0 191.07041068301848,250.0 192.5375637893775,250.0 194.0047168957365,250.0 195.47187000209547,250.0 196.93902310845453,250.0 198.4061762148135,250.0 199.87332932117252,250.0 201.34048242753153,250.0 202.80763553389056,250.0 204.27478864024957,250.0 205.74194174660857,250.0 207.20909485296758,250.0 208.6762479593266,250.0 210.14340106568562,250.0 211.6105541720446,250.0 213.0777072784036,250.0 214.54486038476261,250.0 216.01201349112165,250.0 217.47916659748066,250.0 218.9463197038397,250.0 220.41347281019867,250.0 221.8806259165577,250.0 223.34777902291668,250.0 224.8149321292757,250.0 226.28208523563475,250.0 227.74923834199376,250.0 229.21639144835277,250.0 230.68354455471174,250.0 232.15069766107078,250.0 233.6178507674298,250.0 235.0850038737888,250.0 236.55215698014777,250.0 238.01931008650678,250.0 239.48646319286584,250.0 240.95361629922485,250.0 242.42076940558383,250.0 243.88792251194286,250.0 245.35507561830187,250.0 246.82222872466087,250.0 248.28938183101988,250.0 249.75653493737892,250.0 251.22368804373792,250.0 252.69084115009696,250.0 254.15799425645594,250.0 255.62514736281491,250.0 257.09230046917395,250.0 258.559453575533,250.0 258.559453575533,247.9043444706895 257.09230046917395,247.5466876306466 255.62514736281491,247.13721186484685 254.15799425645594,246.67011697218646 252.69084115009696,246.13924576690744 251.22368804373792,245.53811118591932 249.75653493737892,244.8599334657521 248.28938183101988,244.09768822142442 246.82222872466087,243.24416612721362 245.35507561830187,242.2920447271762 243.88792251194286,241.23397269050957 242.42076940558383,240.06266657395489 240.95361629922485,238.771019862361 239.48646319286584,237.3522237327816 238.01931008650678,235.7998986322748 236.55215698014777,234.1082353818376 235.0850038737888,232.27214412725255 233.6178507674298,230.28740906225738 232.15069766107078,228.1508464619847 230.68354455471174,225.86046319782955 229.21639144835277,223.4156125723773 227.74923834199376,220.81714402875608 226.28208523563475,218.06754306669873 224.8149321292757,215.1710575510533 223.34777902291668,212.13380653965962 221.8806259165577,208.96386779690

### Assess model fit

In [165]:
def rmse(predictions, targets):
    differences = predictions - targets                       #the DIFFERENCEs.
    differences_squared = differences ** 2                    #the SQUAREs of ^
    mean_of_differences_squared = differences_squared.mean()  #the MEAN of ^
    rmse_val = np.sqrt(mean_of_differences_squared)           #ROOT of ^
    return rmse_val   

In [166]:
def aicm(mean, variance):
    return 2*mean - 2*variance

In [167]:
rmse(unpooled_sub['trace']['𝜓'].mean(axis=0), SPECIES_DATA['psi'])

0.9384409617057597

In [168]:
rmse(partpooled_sub['trace']['𝜓'].mean(axis=0), SPECIES_DATA['psi_x'])

0.6105422350829149

In [177]:
aicm(unpooled_sub['trace']['𝜓'].mean(), unpooled_sub['trace']['𝜓'].var())

-24.454868204001738

In [179]:
# Raftery et al. (2007) holds that this value is better.  R+M disagree?
aicm(partpooled_sub['trace']['𝜓'].mean(), partpooled_sub['trace']['𝜓'].var())

-12.49733802346165

In [44]:
az_pooled_model_pooled_data = az.from_pymc3(trace = pooled_model_pooled_data['trace'], 
                                            model = pooled_model_pooled_data['model'])
az_pooled_model_unpooled_data = az.from_pymc3(trace = pooled_model_unpooled_data['trace'], 
                                            model = pooled_model_unpooled_data['model'])
az_pooled_model_partpooled_data = az.from_pymc3(trace = pooled_model_partpooled_data['trace'], 
                                            model = pooled_model_partpooled_data['model'])
az_unpooled_model_pooled_data = az.from_pymc3(trace = unpooled_model_pooled_data['trace'], 
                                            model = unpooled_model_pooled_data['model'])
az_unpooled_model_unpooled_data = az.from_pymc3(trace = unpooled_model_unpooled_data['trace'], 
                                            model = unpooled_model_unpooled_data['model'])
az_unpooled_model_partpooled_data = az.from_pymc3(trace = unpooled_model_partpooled_data['trace'], 
                                            model = unpooled_model_partpooled_data['model'])
az_partpooled_model_pooled_data = az.from_pymc3(trace = partpooled_model_pooled_data['trace'], 
                                            model = partpooled_model_pooled_data['model'])
az_partpooled_model_unpooled_data = az.from_pymc3(trace = partpooled_model_unpooled_data['trace'], 
                                            model = partpooled_model_unpooled_data['model'])
az_partpooled_model_partpooled_data = az.from_pymc3(trace = partpooled_model_partpooled_data['trace'], 
                                            model = partpooled_model_partpooled_data['model'])

### Comapre models with different datasets

In [45]:
az.compare({"pooled_model_pooled_data": az_pooled_model_pooled_data,
            "pooled_model_unpooled_data": az_pooled_model_unpooled_data, 
            "pooled_model_partpooled_data": az_pooled_model_partpooled_data})

/home/henry/miniconda3/envs/py37/lib/python3.7/site-packages/arviz/stats/stats.py:150: UserWarning: 
The scale is now log by default. Use 'scale' argument or 'stats.ic_scale' rcParam if you rely on a specific value.
A higher log-score (or a lower deviance) indicates a model with better predictive accuracy.
  "\nThe scale is now log by default. Use 'scale' argument or "


rank      loo    p_loo    d_loo     weight  \
pooled_model_partpooled_data    0 -723.035  2.01829        0   0.544607   
pooled_model_pooled_data        1   -728.4  2.02015  5.36469   0.434177   
pooled_model_unpooled_data      2 -785.804  2.04918  62.7687  0.0212158   

                                   se      dse warning loo_scale  
pooled_model_partpooled_data  29.0946        0   False       log  
pooled_model_pooled_data      30.1182  41.4887   False       log  
pooled_model_unpooled_data    28.9102  41.3246   False       log

In [46]:
az.compare({"unpooled_model_pooled_data": az_unpooled_model_pooled_data,
            "unpooled_model_unpooled_data": az_unpooled_model_unpooled_data, 
            "unpooled_model_partpooled_data": az_unpooled_model_partpooled_data})

/home/henry/miniconda3/envs/py37/lib/python3.7/site-packages/arviz/stats/stats.py:150: UserWarning: 
The scale is now log by default. Use 'scale' argument or 'stats.ic_scale' rcParam if you rely on a specific value.
A higher log-score (or a lower deviance) indicates a model with better predictive accuracy.
  "\nThe scale is now log by default. Use 'scale' argument or "


rank      loo    p_loo    d_loo     weight  \
unpooled_model_partpooled_data    0 -723.942   6.6022        0   0.512269   
unpooled_model_pooled_data        1 -728.759  14.7659  4.81722   0.462989   
unpooled_model_unpooled_data      2 -786.479  9.65908  62.5368  0.0247418   

                                     se      dse warning loo_scale  
unpooled_model_partpooled_data  29.1288        0   False       log  
unpooled_model_pooled_data      27.5301  41.5763   False       log  
unpooled_model_unpooled_data    28.7416  41.3661   False       log

In [47]:
az.compare({"partpooled_model_pooled_data": az_partpooled_model_pooled_data,
            "partpooled_model_unpooled_data": az_partpooled_model_unpooled_data, 
            "partpooled_model_partpooled_data": az_partpooled_model_partpooled_data})

/home/henry/miniconda3/envs/py37/lib/python3.7/site-packages/arviz/stats/stats.py:150: UserWarning: 
The scale is now log by default. Use 'scale' argument or 'stats.ic_scale' rcParam if you rely on a specific value.
A higher log-score (or a lower deviance) indicates a model with better predictive accuracy.
  "\nThe scale is now log by default. Use 'scale' argument or "


rank      loo    p_loo    d_loo     weight  \
partpooled_model_partpooled_data    0 -728.756  17.3979        0   0.516612   
partpooled_model_pooled_data        1 -731.448  23.0622   2.6929   0.463147   
partpooled_model_unpooled_data      2 -789.655  20.4133  60.8994  0.0202408   

                                       se      dse warning loo_scale  
partpooled_model_partpooled_data  28.3625        0   False       log  
partpooled_model_pooled_data      29.8762   41.601   False       log  
partpooled_model_unpooled_data    28.0529  41.5167   False       log

### Compare datasets with different models

In [53]:
az.compare({"pooled_model_pooled_data": az_pooled_model_pooled_data,
            "unpooled_model_pooled_data": az_unpooled_model_pooled_data, 
            "partpooled_model_pooled_data": az_partpooled_model_pooled_data})

/home/henry/miniconda3/envs/py37/lib/python3.7/site-packages/arviz/stats/stats.py:150: UserWarning: 
The scale is now log by default. Use 'scale' argument or 'stats.ic_scale' rcParam if you rely on a specific value.
A higher log-score (or a lower deviance) indicates a model with better predictive accuracy.
  "\nThe scale is now log by default. Use 'scale' argument or "


rank      loo    p_loo     d_loo     weight  \
pooled_model_pooled_data        0   -728.4  2.02015         0   0.539778   
unpooled_model_pooled_data      1 -728.759  14.7659  0.359453   0.366852   
partpooled_model_pooled_data    2 -731.448  23.0622   3.04863  0.0933704   

                                   se      dse warning loo_scale  
pooled_model_pooled_data      29.1304        0   False       log  
unpooled_model_pooled_data    29.2428   1.4256   False       log  
partpooled_model_pooled_data  29.2191  2.92427   False       log

In [54]:
az.compare({"pooled_model_unpooled_data": az_pooled_model_unpooled_data,
            "unpooled_model_unpooled_data": az_unpooled_model_unpooled_data, 
            "partpooled_model_unpooled_data": az_partpooled_model_unpooled_data})

/home/henry/miniconda3/envs/py37/lib/python3.7/site-packages/arviz/stats/stats.py:150: UserWarning: 
The scale is now log by default. Use 'scale' argument or 'stats.ic_scale' rcParam if you rely on a specific value.
A higher log-score (or a lower deviance) indicates a model with better predictive accuracy.
  "\nThe scale is now log by default. Use 'scale' argument or "


rank      loo    p_loo     d_loo     weight  \
pooled_model_unpooled_data        0 -785.804  2.04918         0    0.59345   
unpooled_model_unpooled_data      1 -786.479  9.65908  0.675015   0.319899   
partpooled_model_unpooled_data    2 -789.655  20.4133   3.85108  0.0866514   

                                     se      dse warning loo_scale  
pooled_model_unpooled_data      28.7965        0   False       log  
unpooled_model_unpooled_data    28.7993  0.83034   False       log  
partpooled_model_unpooled_data  28.7951  2.79555   False       log

In [55]:
az.compare({"pooled_model_partpooled_data": az_pooled_model_partpooled_data,
            "unpooled_model_partpooled_data": az_unpooled_model_partpooled_data, 
            "partpooled_model_partpooled_data": az_partpooled_model_partpooled_data})

/home/henry/miniconda3/envs/py37/lib/python3.7/site-packages/arviz/stats/stats.py:150: UserWarning: 
The scale is now log by default. Use 'scale' argument or 'stats.ic_scale' rcParam if you rely on a specific value.
A higher log-score (or a lower deviance) indicates a model with better predictive accuracy.
  "\nThe scale is now log by default. Use 'scale' argument or "


rank      loo    p_loo     d_loo     weight  \
pooled_model_partpooled_data        0 -723.035  2.01829         0   0.700747   
unpooled_model_partpooled_data      1 -723.942   6.6022  0.906921   0.289025   
partpooled_model_partpooled_data    2 -728.756  17.3979   5.72042  0.0102273   

                                       se       dse warning loo_scale  
pooled_model_partpooled_data      28.4664         0   False       log  
unpooled_model_partpooled_data    28.4913  0.483591   False       log  
partpooled_model_partpooled_data  28.5985   2.07422   False       log

### other stuff

In [49]:
# Save trace.  To load in different notebook, model context and sample data is required.
pm.save_trace(partpooled_model_partpooled_data['trace'], directory = "/home/henry/oaks-thesis/trace/exponential-pmpd")

'/home/henry/oaks-thesis/trace/exponential-pmpd'

In [50]:
exponential_args = [
    SAMPLE.dist,
    SAMPLE.RI_partpooled,
    SAMPLE.sidx0,
    SAMPLE.sidx1,
    gidx
]

In [51]:
%store exponential_args

Stored 'exponential_args' (list)
